# Examples

In [1]:
%load_ext autoreload
%autoreload 2

from hourly_simulation import strategies
from output_graphs.hourly_graph_creator import *
from hourly_simulation.parameters import *
from df_objects.df_objects import *
from hourly_simulation.predict_demand import predict_demand_in_year
from tests.sanity_checks import test_simulation
import logging
logging.getLogger().setLevel(logging.INFO)

## Daily Constant demand different production profiles

In [12]:

battery_capacity = 1
battery_power = 1
print("*Under production*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [9] * 24}))
electricity_use: ElectricityUseDf = strategies.better_use_strategy(future_demand, total_panel_production,
                                                                   battery_capacity, battery_power)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                battery_capacity=battery_capacity)
daily_graph(electricity_use.df)

print("*Over production*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [11] * 24}))
electricity_use: ElectricityUseDf = strategies.better_use_strategy(future_demand, total_panel_production,
                                                                   battery_capacity, battery_power)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                battery_capacity=battery_capacity)
daily_graph(electricity_use.df)

print("*Oscillations around demand*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [10 + 2 * np.sin(2 * np.pi * x / 6)
                                                                                      for x in range(24)]}))
electricity_use: ElectricityUseDf = strategies.better_use_strategy(future_demand, total_panel_production,
                                                                   battery_capacity, battery_power)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                battery_capacity=battery_capacity)
daily_graph(electricity_use.df)


INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:Passed all tests


*Under production*


INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:Passed all tests


*Over production*


INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:Passed all tests


*Oscillations around demand*


## Yearly Constant demand and sinus production around demand

In [4]:
battery_capacity = 1
future_demand = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(8760)],
                                       "Demand": [10] * 8760}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(8760)],
                                                                  "SolarProduction": [10 + 2 * np.sin(2 * np.pi * x / 6)
                                                                                      for x in range(8760)]}))
electricity_use: ElectricityUseDf = strategies.better_use_strategy(future_demand, total_panel_production,
                                                                   battery_capacity)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                battery_capacity=battery_capacity)
yearly_graph(electricity_use.df)

INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:Passed all tests


In [46]:
num_batteries = 3.447368
solar_panel_power_kw = 6000
demand = DemandDf(pd.read_csv(r'../data/consumption_hatzor.csv', index_col=0))
future_demand = predict_demand_in_year(demand, 2020)
total_panel_production = ProductionDf(NORMALISED_SOLAR_PRODUCTION.df.copy())
total_panel_production.df[total_panel_production.SolarProduction] *= solar_panel_power_kw
electricity_use: ElectricityUseDf = strategies.better_use_strategy(future_demand, total_panel_production,
                                                                   BATTERY_CAPACITY * num_batteries, CHARGE_POWER * num_batteries)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                num_batteries=num_batteries)
yearly_graph(electricity_use.df, num_hours_to_sum=1)

INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:Passed all tests


In [37]:
from hourly_simulation.simulation import *
from tqdm import tqdm

solar_panel_power_it = np.linspace(5500, 6500, 20)
num_batteries_it = np.linspace(2.5, 4.5, 20)
demand = DemandDf(pd.read_csv(r'../data/consumption_hatzor.csv', index_col=0))
single_panel_production = ProductionDf(NORMALISED_SOLAR_PRODUCTION.df.copy())
simulated_year = 2020

simulation_results = {'PowerSolar': [], 'BatteryCapacity': [], 'Cost': []}
for power_solar_panels in tqdm(solar_panel_power_it):
    for num_batteries in num_batteries_it:
        simulation_results['PowerSolar'].append(power_solar_panels)
        simulation_results['BatteryCapacity'].append(num_batteries)
        simulation_results['Cost'].append(simulate_use(demand, single_panel_production, power_solar_panels, num_batteries, strategies.better_use_strategy,simulated_year, time_span=25))

df_results = pd.DataFrame.from_dict(simulation_results)
print(str(df_results.loc[df_results['Cost'].idxmin()]))

100%|██████████| 20/20 [00:18<00:00,  1.08it/s]

PowerSolar         6.078947e+03
BatteryCapacity    3.447368e+00
Cost               2.821832e+06
Name: 229, dtype: float64


In [44]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np

xx = df_results.PowerSolar.to_numpy().reshape(len(solar_panel_power_it), -1)
yy = df_results.BatteryCapacity.to_numpy().reshape(-1, len(num_batteries_it))
z = df_results.Cost.to_numpy().reshape(len(solar_panel_power_it), len(num_batteries_it))

fig = make_subplots(rows=1, cols=2, specs=[[{'type': 'scatter'}, {'type': 'scene'}]])

fig.add_traces(data = [
    go.Contour(z=z, x=num_batteries_it, y=solar_panel_power_it, colorscale='Electric', showscale=False),
    go.Surface(x=num_batteries_it, y= solar_panel_power_it, z=z, opacity=.8, colorscale='Electric', contours=dict(z=dict(show=True)))],
    rows=[1,1], cols=[1,2])
fig.update_xaxes(title_text="N batteries", row=1, col=1)
fig.update_yaxes(title_text="Max solar panel power kw", row=1, col=1)


# fig.update_layout(width=800, height=300, scene_aspectmode="cube", scene=dict(camera = dict(eye=dict(x=-1.5, y=-1.5, z=.2))))
fig.show()